# Question Generator for Coronabot

## Define question templates and required parameters

In [1]:
templates = [
        { 
            "last": True,
            "questions": [
                "How many cases were reported in August in Magdeburg?" # static by intention
            ],
            "parameters": {
                "QUESTION_CLASS": "infection_location_time",
                "CONTAINS_TIME": True
            }
        },
        {
            "last": True,
            "questions": [
                "What was the death toll in [PLACE_LABEL] during the last [MONTH]?",
                "How many people died in [PLACE_LABEL] last [MONTH]?",
                "How many deaths were reported last [MONTH] in [PLACE_LABEL]?",
                "covid deaths in [PLACE_LABEL] last [MONTH]",
                "how many deaths did [PLACE_LABEL] have last [MONTH]?"
            ],
            "parameters": {
                "QUESTION_CLASS": "death_location_time",
                "CONTAINS_TIME": True
            }
        },
        {
            "last": False,
            "questions": [
                "What was the death toll in [PLACE_LABEL] during [MONTH] of [YEAR]?",
                "How many people died in [PLACE_LABEL] in [MONTH] [YEAR]?",
                "How many deaths were reported in [PLACE_LABEL] in [MONTH] [YEAR]?",
                "covid deaths in [PLACE_LABEL] in [MONTH] of [YEAR]",
                "how many deaths did [PLACE_LABEL] have in [MONTH] [YEAR]?"
            ],
            "parameters": {
                "QUESTION_CLASS": "death_location_time",
                "CONTAINS_TIME": True
            }
        },
        {
            "last": False,
            "questions": [
                "How many infections were there in [PLACE_LABEL] in [MONTH] [YEAR]?",
                "In [MONTH] [YEAR], how many people were infected in [PLACE_LABEL]?",
                "Give me the number of cases in [PLACE_LABEL] during [MONTH] [YEAR]!",
                "How many cases of Covid did [PLACE_LABEL] report in [MONTH] [YEAR]?",
                "infections in [MONTH] [YEAR] in [PLACE_LABEL]"
            ],
            "parameters": {
                "QUESTION_CLASS": "infection_location_time",
                "CONTAINS_TIME": True
            }
        },
        {
            "last": False,
            "questions": [
                "What was the number of incidents of [PLACE_LABEL] in [YEAR]?"
            ],
            "parameters": {
                "QUESTION_CLASS": "infection_location_time",
                "CONTAINS_TIME": True
            }
        },
        {
            "last": False,
            "questions": [
                "How many people died in [PLACE_LABEL]?",
                "How many deaths were reported in [PLACE_LABEL]?",
                "covid deaths in [PLACE_LABEL]",
                "What is the current death toll in [PLACE_LABEL]?"
            ],
            "parameters": {
                "QUESTION_CLASS": "death_location",
                "CONTAINS_TIME": False
            }
        },       
        {
            "last": False,
            "questions": [
                "How many people died during [MONTH] [YEAR]?",
                "How many deaths were reported in [MONTH] of [YEAR]?",
                "covid deaths on the fith of [MONTH] [YEAR]",
                "What was the death toll during [MONTH] [YEAR]?",
                "number of deaths from first of [MONTH] until 15th of [MONTH] [YEAR]"
            ],
            "parameters": {
                "QUESTION_CLASS": "death_time",
                "CONTAINS_TIME": True
            }
        }, 
        {
            "last": True,
            "questions": [
                "How many people died during last [MONTH]?",
                "How many deaths were reported in last [MONTH]?",
                "covid deaths on the fith of last [MONTH]",
                "What was the death toll last [MONTH]?",
                "number of deaths from the first until the 15th of last [MONTH]"
            ],
            "parameters": {
                "QUESTION_CLASS": "death_time",
                "CONTAINS_TIME": True
            }
        },
        {
            "last": False,
            "questions": [
                "How many cases were reported on the first of [MONTH] [YEAR]?",
                "What was the number of infections during [MONTH] [YEAR]?",
                "infections between the first of [MONTH] [YEAR] and the 28th of [MONTH] [YEAR]?",
                "How many people were infected with Covid-19 in [MONTH] [YEAR]",
                "corona cases in [MONTH] [YEAR]"
            ],
            "parameters": {
                "QUESTION_CLASS": "infection_time",
                "CONTAINS_TIME": True
            }
        }, 
        {
            "last": True,
            "questions": [
                "How many cases were reported on the first of last [MONTH]?",
                "What was the number of infections last [MONTH]?",
                "infections between the first and 28th of last [MONTH]?",
                "How many people were infected with Covid-19 last [MONTH]",
                "corona cases last [MONTH]"
            ],
            "parameters": {
                "QUESTION_CLASS": "infection_time",
                "CONTAINS_TIME": True
            }
        },
        {
            "last": False,
            "questions": [
                "Infections in [PLACE_LABEL] and Kiel?",
                "Cases in [PLACE_LABEL]?",
                "How many people have been infected in [PLACE_LABEL] in total?",
                "[PLACE_LABEL] corona cases",
                "give me the number of infections in [PLACE_LABEL]"
            ],
            "parameters": {
                "QUESTION_CLASS": "infection_location",
                "CONTAINS_TIME": False
            }
        }        
]

parameters = {
    "MONTH": ["January", "February", "March", "April", "May", "June", "July", "August", "September", "October", "November", "December"],
    "YEAR": [2020, 2021],
    "PLACE_LABEL": [],
    "PLACE_URL": [],
    "LANGUAGE": ["en"]
}

### add places from Wikidata

In [2]:
from pprint import pprint
from SPARQLWrapper import SPARQLWrapper, JSON # https://sparqlwrapper.readthedocs.io/en/latest/main.html

sparql = SPARQLWrapper("https://query.wikidata.org/bigdata/namespace/wdq/sparql")
sparql.setQuery("""
# get all districts

PREFIX wd: <http://www.wikidata.org/entity/>
PREFIX wdt: <http://www.wikidata.org/prop/direct/>
PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
PREFIX p: <http://www.wikidata.org/prop/>
PREFIX ps: <http://www.wikidata.org/prop/statement/>
PREFIX pq: <http://www.wikidata.org/prop/qualifier/>

SELECT DISTINCT ?district ?label WHERE {
  #VALUES ?district { wd:Q6098 } .
  ?district p:P31/ps:P31/wdt:P279* wd:Q106658 .
  ?district wdt:P17 wd:Q183 .
  ?district rdfs:label ?label .
  FILTER (LANG(?label) = "en").
} 
LIMIT 1000
""")
sparql.setReturnFormat(JSON)
results = sparql.query().convert()
# pprint(results)

place_values = []
place_names_map = {}
for result in results["results"]["bindings"]:
    # print(result["label"]["value"], result["district"]["value"])
    place_values.append(result["label"]["value"])
    place_names_map[result["label"]["value"]] = result["district"]["value"]

pprint(place_names_map)
parameters["PLACE_LABEL"] = place_values
parameters["PLACE_URL"] = place_names_map
number=len(parameters["PLACE_LABEL"])
print(f"number of found places: {number}")


{'Aachen': 'http://www.wikidata.org/entity/Q7379734',
 'Aachen cities region': 'http://www.wikidata.org/entity/Q6272',
 'Ahaus District': 'http://www.wikidata.org/entity/Q878419',
 'Ahrweiler': 'http://www.wikidata.org/entity/Q8596',
 'Aichach': 'http://www.wikidata.org/entity/Q1756892',
 'Aichach-Friedberg': 'http://www.wikidata.org/entity/Q10415',
 'Alb-Donau-Kreis': 'http://www.wikidata.org/entity/Q8221',
 'Alfeld': 'http://www.wikidata.org/entity/Q1803052',
 'Alsfeld': 'http://www.wikidata.org/entity/Q1803054',
 'Altena District': 'http://www.wikidata.org/entity/Q1803056',
 'Altenburger Land': 'http://www.wikidata.org/entity/Q7888',
 'Altenkirchen district': 'http://www.wikidata.org/entity/Q8608',
 'Altlandkreis Kulmbach': 'http://www.wikidata.org/entity/Q105729117',
 'Altlandkreis Lichtenfels': 'http://www.wikidata.org/entity/Q105744572',
 'Altmarkkreis Salzwedel': 'http://www.wikidata.org/entity/Q6061',
 'Altötting': 'http://www.wikidata.org/entity/Q10533',
 'Alzey-Worms': 'http:

## Generate questions

In [3]:
import time
import random
random.seed(round(time.time() * 1000))

def get_random_parameters(parameters):
    result = {}
    for k in parameters.keys():
        if k != "PLACE_URL": # TODO: needs to be generalized
            random_key = random.randint(0,len(parameters[k])-1)
            try:
                result[k] = parameters[k][random_key]
            except Exception as e:
                print(f"random_key: {random_key}")
                pprint(parameters[k])
                raise e
        else:
            pass # skip should only happen in case of dependent values

    result["PLACE_URL"] = parameters["PLACE_URL"][result["PLACE_LABEL"]] # TODO: needs to be generalized

    return result

def get_random_list_of_templates_questions(questions, number_of_questions_to_be_selected):
    randomly_selected_questions = []
    number_of_available_questions = len(questions)
    for i in range(number_of_questions_to_be_selected):
        random_key = random.randint(0,number_of_available_questions-1)
        randomly_selected_questions.append(questions[random_key])
    return randomly_selected_questions

generated_questions = []

random_templates = get_random_list_of_templates_questions(templates, 1000)
for template in random_templates:
    questions = template["questions"]
    for question in questions:
        concrete_parameters = get_random_parameters(parameters)
        for place_holder, concrete_instance in concrete_parameters.items():
            question = question.replace('['+place_holder+']', str(concrete_instance))

        concrete_parameters_merged = {}
        if template.get("parameters", None) != None: # there might be predefined parameters of the question template
            concrete_parameters_merged = {**template.get("parameters"), **concrete_parameters}
        else:
            concrete_parameters_merged = concrete_parameters
        generated_question_configuration = {"question": question, "replacements": concrete_parameters_merged, "template": template}

        generated_questions.append(generated_question_configuration)


pprint(generated_questions, width=120)

generated_configuration = {}
generated_configuration["qanary"] = {
    "system_url": "https://webengineering.ins.hs-anhalt.de:43740/startquestionansweringwithtextquestion",
    "componentlist": ["LD-Shuyo", "coronabot-dialog-flow", "coronabot-question-classification", "coronabot-named-entity-recognition-time-en", "coronabot-named-entity-recognition-time-de", "coronabot-named-entity-recognition-location-en", "coronabot-named-entity-recognition-location-de", "OpenTapiocaNED", "LocationToGermanDistrict", "coronabot-missing-information", "coronabot-query-generation", "coronabot-data-acquisition", "coronabot-answer-generation"],
    "qanary_triplestore_endpoint": "https://webengineering.ins.hs-anhalt.de:40159",
    "qanary_triplestore_database": "qanary",
    "qanary_triplestore_username": "admin",
    "qanary_triplestore_password": "admin"
}
generated_configuration["tests"] = generated_questions
generated_configuration["validation-sparql-templates"] = ["01_language_detection.sparql","02_question_classification.sparql", "03_time_recognition.sparql", "04_ned.sparql", "05_location_to_german_district.sparql", "06_coronabot_missing_information.sparql", "07_rki_query.sparql"]
# generated_configuration["custom-validation"] = "dummy" # should not be defined if not required

pprint(generated_configuration, width=120)


[{'question': 'How many people died during September 2020?',
  'replacements': {'CONTAINS_TIME': True,
                   'LANGUAGE': 'en',
                   'MONTH': 'September',
                   'PLACE_LABEL': 'Altenburger Land',
                   'PLACE_URL': 'http://www.wikidata.org/entity/Q7888',
                   'QUESTION_CLASS': 'death_time',
                   'YEAR': 2020},
  'template': {'last': False,
               'parameters': {'CONTAINS_TIME': True, 'QUESTION_CLASS': 'death_time'},
               'questions': ['How many people died during [MONTH] [YEAR]?',
                             'How many deaths were reported in [MONTH] of [YEAR]?',
                             'covid deaths on the fith of [MONTH] [YEAR]',
                             'What was the death toll during [MONTH] [YEAR]?',
                             'number of deaths from first of [MONTH] until 15th of [MONTH] [YEAR]']}},
 {'question': 'How many deaths were reported in March of 2021?',
  'replace

 {'question': 'infections between the first and 28th of last January?',
  'replacements': {'CONTAINS_TIME': True,
                   'LANGUAGE': 'en',
                   'MONTH': 'January',
                   'PLACE_LABEL': 'Münster District',
                   'PLACE_URL': 'http://www.wikidata.org/entity/Q878752',
                   'QUESTION_CLASS': 'infection_time',
                   'YEAR': 2020},
  'template': {'last': True,
               'parameters': {'CONTAINS_TIME': True, 'QUESTION_CLASS': 'infection_time'},
               'questions': ['How many cases were reported on the first of last [MONTH]?',
                             'What was the number of infections last [MONTH]?',
                             'infections between the first and 28th of last [MONTH]?',
                             'How many people were infected with Covid-19 last [MONTH]',
                             'corona cases last [MONTH]']}},
 {'question': 'How many people were infected with Covid-19 last Ju

                   'LANGUAGE': 'en',
                   'MONTH': 'March',
                   'PLACE_LABEL': 'Pegnitz',
                   'PLACE_URL': 'http://www.wikidata.org/entity/Q1445349',
                   'QUESTION_CLASS': 'death_location_time',
                   'YEAR': 2020},
  'template': {'last': True,
               'parameters': {'CONTAINS_TIME': True, 'QUESTION_CLASS': 'death_location_time'},
               'questions': ['What was the death toll in [PLACE_LABEL] during the last [MONTH]?',
                             'How many people died in [PLACE_LABEL] last [MONTH]?',
                             'How many deaths were reported last [MONTH] in [PLACE_LABEL]?',
                             'covid deaths in [PLACE_LABEL] last [MONTH]',
                             'how many deaths did [PLACE_LABEL] have last [MONTH]?']}},
 {'question': 'covid deaths in Grevenbroich District last February',
  'replacements': {'CONTAINS_TIME': True,
                   'LANGUAGE': 'en',
  

               'questions': ['How many people died in [PLACE_LABEL]?',
                             'How many deaths were reported in [PLACE_LABEL]?',
                             'covid deaths in [PLACE_LABEL]',
                             'What is the current death toll in [PLACE_LABEL]?']}},
 {'question': 'covid deaths in Anhalt-Zerbst',
  'replacements': {'CONTAINS_TIME': False,
                   'LANGUAGE': 'en',
                   'MONTH': 'May',
                   'PLACE_LABEL': 'Anhalt-Zerbst',
                   'PLACE_URL': 'http://www.wikidata.org/entity/Q114369',
                   'QUESTION_CLASS': 'death_location',
                   'YEAR': 2021},
  'template': {'last': False,
               'parameters': {'CONTAINS_TIME': False, 'QUESTION_CLASS': 'death_location'},
               'questions': ['How many people died in [PLACE_LABEL]?',
                             'How many deaths were reported in [PLACE_LABEL]?',
                             'covid deaths in [PLACE_LA

                             'How many people died in [PLACE_LABEL] in [MONTH] [YEAR]?',
                             'How many deaths were reported in [PLACE_LABEL] in [MONTH] [YEAR]?',
                             'covid deaths in [PLACE_LABEL] in [MONTH] of [YEAR]',
                             'how many deaths did [PLACE_LABEL] have in [MONTH] [YEAR]?']}},
 {'question': 'covid deaths in Mühldorf in April of 2021',
  'replacements': {'CONTAINS_TIME': True,
                   'LANGUAGE': 'en',
                   'MONTH': 'April',
                   'PLACE_LABEL': 'Mühldorf',
                   'PLACE_URL': 'http://www.wikidata.org/entity/Q10537',
                   'QUESTION_CLASS': 'death_location_time',
                   'YEAR': 2021},
  'template': {'last': False,
               'parameters': {'CONTAINS_TIME': True, 'QUESTION_CLASS': 'death_location_time'},
               'questions': ['What was the death toll in [PLACE_LABEL] during [MONTH] of [YEAR]?',
                         

...

                             'PLACE_LABEL': 'Ostprignitz-Ruppin District',
                             'PLACE_URL': 'http://www.wikidata.org/entity/Q6125',
                             'QUESTION_CLASS': 'death_time',
                             'YEAR': 2020},
            'template': {'last': True,
                         'parameters': {'CONTAINS_TIME': True, 'QUESTION_CLASS': 'death_time'},
                         'questions': ['How many people died during last [MONTH]?',
                                       'How many deaths were reported in last [MONTH]?',
                                       'covid deaths on the fith of last [MONTH]',
                                       'What was the death toll last [MONTH]?',
                                       'number of deaths from the first until the 15th of last [MONTH]']}},
           {'question': 'How many deaths were reported in last April?',
            'replacements': {'CONTAINS_TIME': True,
                             'LANGU

            'replacements': {'CONTAINS_TIME': True,
                             'LANGUAGE': 'en',
                             'MONTH': 'September',
                             'PLACE_LABEL': 'Güstrow',
                             'PLACE_URL': 'http://www.wikidata.org/entity/Q559600',
                             'QUESTION_CLASS': 'death_location_time',
                             'YEAR': 2021},
            'template': {'last': False,
                         'parameters': {'CONTAINS_TIME': True, 'QUESTION_CLASS': 'death_location_time'},
                         'questions': ['What was the death toll in [PLACE_LABEL] during [MONTH] of [YEAR]?',
                                       'How many people died in [PLACE_LABEL] in [MONTH] [YEAR]?',
                                       'How many deaths were reported in [PLACE_LABEL] in [MONTH] [YEAR]?',
                                       'covid deaths in [PLACE_LABEL] in [MONTH] of [YEAR]',
                                       'how

                             'PLACE_URL': 'http://www.wikidata.org/entity/Q6057',
                             'QUESTION_CLASS': 'infection_time',
                             'YEAR': 2021},
            'template': {'last': False,
                         'parameters': {'CONTAINS_TIME': True, 'QUESTION_CLASS': 'infection_time'},
                         'questions': ['How many cases were reported on the first of [MONTH] [YEAR]?',
                                       'What was the number of infections during [MONTH] [YEAR]?',
                                       'infections between the first of [MONTH] [YEAR] and the 28th of [MONTH] [YEAR]?',
                                       'How many people were infected with Covid-19 in [MONTH] [YEAR]',
                                       'corona cases in [MONTH] [YEAR]']}},
           {'question': 'How many people were infected with Covid-19 in April 2021',
            'replacements': {'CONTAINS_TIME': True,
                             

                         'questions': ['How many cases were reported on the first of [MONTH] [YEAR]?',
                                       'What was the number of infections during [MONTH] [YEAR]?',
                                       'infections between the first of [MONTH] [YEAR] and the 28th of [MONTH] [YEAR]?',
                                       'How many people were infected with Covid-19 in [MONTH] [YEAR]',
                                       'corona cases in [MONTH] [YEAR]']}},
           {'question': 'What was the number of incidents of Vorpommern-Greifswald District in 2020?',
            'replacements': {'CONTAINS_TIME': True,
                             'LANGUAGE': 'en',
                             'MONTH': 'July',
                             'PLACE_LABEL': 'Vorpommern-Greifswald District',
                             'PLACE_URL': 'http://www.wikidata.org/entity/Q2917',
                             'QUESTION_CLASS': 'infection_location_time',
               

                             'QUESTION_CLASS': 'death_location_time',
                             'YEAR': 2021},
            'template': {'last': True,
                         'parameters': {'CONTAINS_TIME': True, 'QUESTION_CLASS': 'death_location_time'},
                         'questions': ['What was the death toll in [PLACE_LABEL] during the last [MONTH]?',
                                       'How many people died in [PLACE_LABEL] last [MONTH]?',
                                       'How many deaths were reported last [MONTH] in [PLACE_LABEL]?',
                                       'covid deaths in [PLACE_LABEL] last [MONTH]',
                                       'how many deaths did [PLACE_LABEL] have last [MONTH]?']}},
           {'question': 'covid deaths in Lüchow-Dannenberg District last July',
            'replacements': {'CONTAINS_TIME': True,
                             'LANGUAGE': 'en',
                             'MONTH': 'July',
                             

# Output to file

In [4]:
import json 

with open('sparql_test_query_templates/qanary-test-definition.json', 'w') as outfile:
    json.dump(generated_configuration, outfile, indent=4)